In [1]:
# # класс создания общего датасета
# class MoodthemeAudioDataset(Dataset):
#     def __init__(self, data_dir, labels_dict, mel_spectr_func):
        
#         self.data_dir = data_dir
#         self.labels_dict = labels_dict
#         self.mel_spectr_func = mel_spectr_func

#         # множество тегов
#         self.moodthemes = set()
#         for tags in labels_dict.values():
#             self.moodthemes.update(tags)

#         # сортриуем и преобразуем теги в индексы
#         self.moodthemes = sorted(list(self.moodthemes))
#         self.tag_to_idx = {tag: idx for idx, tag in enumerate(self.moodthemes)}
#         self.num_classes = len(self.moodthemes)

#         # собираем аудиофайлы и теги
#         self.audio_files = []
#         self.labels = []
        
#         for folder_name in os.listdir(data_dir):
#             folder_path = os.path.join(data_dir, folder_name)
#             if os.path.isdir(folder_path):
                
#                 for file_name in os.listdir(folder_path):
#                     if self._is_audio_file(file_name):
#                         key = os.path.join(folder_name, file_name)
#                         if key in labels_dict:
#                             full_path = os.path.join(folder_path, file_name)
#                             self.audio_files.append(full_path)
                            
#                             file_tags = labels_dict[key]
#                             multi_hot = self._tags_to_multi_hot(file_tags)
#                             self.labels.append(multi_hot)

#         self._dummy_mel = self._get_dummy_mel_shape()

#     # быстро получает форму мел-спектрограммы
#     def _get_dummy_mel_shape(self):
#         try:
#             dummy_mel = self.mel_spectr_func(self.audio_files[0])
#             return dummy_mel.shape
#         except:
#             return (1, 128, 512) 

#     # проверка является ли файл аудиофайлом
#     def _is_audio_file(self, filename):
#         return filename.lower().endswith(('.wav', '.mp3', '.flac', '.m4a', '.ogg'))
    

#     # преобразует список тегов в multi-hot вектор
#     def _tags_to_multi_hot(self, tags):
#         multi_hot = np.zeros(self.num_classes, dtype=np.float32)
#         for tag in tags:
#             if tag in self.tag_to_idx:
#                 multi_hot[self.tag_to_idx[tag]] = 1.0
#         return multi_hot


#     def get_class_names(self):
#         return self.moodthemes
    
#     def __len__(self):
#         return len(self.audio_files)
    
#     def __getitem__(self, idx):
#         audio_path = self.audio_files[idx]
#         multi_hot_label = self.labels[idx]
        
#         try:
#             # вычисляем мел-спектрограмму
#             mel_spectrogram = self.mel_spectr_func(audio_path)
            
#             # добавляем dimension для канала если нужно
#             if len(mel_spectrogram.shape) == 2:
#                 mel_spectrogram = mel_spectrogram.unsqueeze(0)
            
#             # преобразуем метку в тензор
#             label_tensor = torch.tensor(multi_hot_label, dtype=torch.float32)
            
#             return mel_spectrogram, label_tensor
            
#         except Exception as e:
#             print(f"Error processing {audio_path}: {e}")
#             # возвращаем тензоры правильной формы
#             return torch.zeros(self._dummy_mel), torch.zeros(self.num_classes)

# def preprocess_audio(audio_path, target_sr = 22050) -> torch.Tensor:
#     waveform, sr = torchaudio.load(audio_path, normalize=True, channels_first=True)
#     # уменьшил частоту дискретизации, чтобы ещё меньше датасет весил, а то везде 44100 Гц или почти везде
#     if sr != target_sr:
#         waveform = torchaudio.functional.resample(waveform, sr, target_sr)
    
#     mel_spectrogram = torchaudio.transforms.MelSpectrogram(
#         sample_rate=target_sr,
#         n_mels=128,        
#         n_fft=1024,       
#         hop_length=256,
#         f_min=20,
#         f_max=11025
#     )(waveform)

#     mel_spectrogram = torch.log(mel_spectrogram + 1e-6)

#     return mel_spectrogram[0,:,:512]


    
#     print(f"🔄 Сохраняем данные батчами по {batch_size} samples...")
    
#     all_batches = []
#     current_batch_data = []
#     current_batch_labels = []
    
#     for i in range(len(dataset)):
#         try:
#             data, label = dataset[i]
#             current_batch_data.append(data)
#             current_batch_labels.append(label)
            
#             # Сохраняем батч и очищаем память
#             if len(current_batch_data) >= batch_size:
#                 batch_data = torch.stack(current_batch_data)
#                 batch_labels = torch.stack(current_batch_labels)
                
#                 all_batches.append({
#                     'data': batch_data,
#                     'labels': batch_labels
#                 })
                
#                 # Очищаем текущий батч
#                 current_batch_data = []
#                 current_batch_labels = []
                
#                 # Принудительно очищаем память
#                 if torch.cuda.is_available():
#                     torch.cuda.empty_cache()
                
#                 print(f"Сохранен батч {len(all_batches)} | Samples: {(len(all_batches)) * batch_size}")
        
#         except Exception as e:
#             print(f"Ошибка с sample {i}: {e}")
#             continue
        
#         if (i + 1) % 500 == 0:
#             print(f"Обработано {i + 1}/{len(dataset)} samples")
    
#     # Сохраняем последний неполный батч
#     if current_batch_data:
#         batch_data = torch.stack(current_batch_data)
#         batch_labels = torch.stack(current_batch_labels)
#         all_batches.append({
#             'data': batch_data,
#             'labels': batch_labels
#         })
    
#     # Сохраняем все батчи в один файл
#     torch.save({
#         'batches': all_batches,
#         'total_samples': sum(batch['data'].shape[0] for batch in all_batches),
#         'data_shape': all_batches[0]['data'].shape if all_batches else None,
#         'labels_shape': all_batches[0]['labels'].shape if all_batches else None,
#         'class_names': dataset.get_class_names() if hasattr(dataset, 'get_class_names') else [],
#         'num_classes': dataset.num_classes if hasattr(dataset, 'num_classes') else None
#     }, filename)
    
#     print(f"Все данные сохранены в {filename}")
#     print(f"Всего samples: {sum(batch['data'].shape[0] for batch in all_batches)}")
#     print(f"Батчей: {len(all_batches)}")

# def save_simple_efficient(dataset, filename='../data/processed_data.pth'):
#     """Простой и экономный способ сохранения"""
    
#     print("🔄 Экономное сохранение...")
    
#     # Сохраняем информацию о данных
#     info = {
#         'total_samples': len(dataset),
#         'class_names': dataset.get_class_names() if hasattr(dataset, 'get_class_names') else [],
#         'num_classes': dataset.num_classes if hasattr(dataset, 'num_classes') else None
#     }
    
#     # Сохраняем данные по одному
#     with open(filename, 'wb') as f:
#         # Сначала сохраняем информацию
#         torch.save(info, f)
        
#         # Затем сохраняем каждый sample отдельно
#         for i in range(len(dataset)):
#             try:
#                 data, label = dataset[i]
#                 torch.save({'data': data, 'label': label}, f)
#             except Exception as e:
#                 print(f"❌ Ошибка с sample {i}: {e}")
#                 continue
            
#             if (i + 1) % 1000 == 0:
#                 print(f"📥 Обработано {i + 1}/{len(dataset)} samples")
    
#     print(f"✅ Данные сохранены в {filename}")

# def save_efficient(dataset, filename='../data/efficient_data.pth'):
    
#     print("🔄 Эффективное сохранение...")
    
#     # Сразу собираем все данные в тензоры
#     data_list = []
#     labels_list = []
#     len_dataset = int(len(dataset) * 0.6)

#     batch_size = 1000  # Обрабатываем по 500 samples за раз

#     for i in range(0, len_dataset, batch_size):
                
#         end_idx = min(i + batch_size, len_dataset)
#         batch_data = []
#         batch_labels = []
        
#         for j in range(i, end_idx):
#             try:
#                 data, label = dataset[j]
#                 batch_data.append(data)
#                 batch_labels.append(label)
#             except Exception as e:
#                 print(f"Ошибка с sample {j}: {e}")
#                 continue
        
#         # Конвертируем батч в тензоры
#         if batch_data:
#             batch_data_tensor = torch.stack(batch_data)
#             batch_labels_tensor = torch.stack(batch_labels)
            
#             data_list.append(batch_data_tensor)
#             labels_list.append(batch_labels_tensor)
        
#         print(f"Обработано {end_idx}/{len_dataset}")
    
#     # Объединяем все батчи
#     all_data = torch.cat(data_list)
#     all_labels = torch.cat(labels_list)
    
#     torch.save({
#         'data': all_data,
#         'labels': all_labels,
#         'metadata': {
#             'num_classes': dataset.num_classes if hasattr(dataset, 'num_classes') else all_labels.shape[1],
#             'class_names': dataset.get_class_names() if hasattr(dataset, 'get_class_names') else [],
#             'data_shape': all_data.shape,
#             'labels_shape': all_labels.shape
#         }
#     }, filename) 
    
#     print(f"Данные сохранены в {filename}")
#     print(f"Размер файла: {os.path.getsize(filename) / 1024 / 1024:.2f} MB")
#     print(f"Данные: {all_data.shape}")
#     print(f"Лейблы: {all_labels.shape}")
# #------------------------------------------------------------------------------

# tags_dict = {}
# # открываем подготовленный словрь
# with open("../data/track_tags.pkl", 'rb') as file:
#     tags_dict = pickle.load(file)

# # создаём датасет
# dataset = MoodthemeAudioDataset(
#     data_dir = "../data/train",
#     labels_dict = tags_dict,
#     mel_spectr_func = preprocess_audio
# )

# # save_simple_efficient(dataset, '../data/processed_data.pth')
# save_efficient(dataset, '../data/efficient_data.pth')

In [2]:
import os
import time
import torch
import pickle
import warnings
import torchaudio
import numpy as np
import torch.nn as nn
import torch.nn.functional as F
import matplotlib.pyplot as plt

from tqdm import tqdm
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from torch.utils.data import Subset
from sklearn.metrics import f1_score
from IPython.display import clear_output
from sklearn.model_selection import train_test_split

# убираем предупреждения
warnings.filterwarnings("ignore", message=".*TorchCodec.*")
warnings.filterwarnings("ignore", message=".*StreamingMediaDecoder.*")

# выбираем устройство
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

def preprocess_audio(audio_path, target_sr = 22050) -> torch.Tensor:
    waveform, sr = torchaudio.load(audio_path, normalize=True, channels_first=True)
    # уменьшил частоту дискретизации, чтобы ещё меньше датасет весил, а то везде 44100 Гц или почти везде
    if sr != target_sr:
        waveform = torchaudio.functional.resample(waveform, sr, target_sr)
    
    mel_spectrogram = torchaudio.transforms.MelSpectrogram(
        sample_rate=target_sr,
        n_mels=128,        
        n_fft=1024,       
        hop_length=256,
        f_min=20,
        f_max=11025
    )(waveform)

    mel_spectrogram = torch.log(mel_spectrogram + 1e-6)

    return mel_spectrogram[0,:,:512]

class GPUDatasetWrapper(Dataset):
    def __init__(self, original_dataset, device = 'cuda'):
        self.original_dataset = original_dataset
        self.device = device
        self.gpu_data = []
        self.gpu_labels = []
        
        for i in range(len(original_dataset)):
            data, label = original_dataset[i]
            
            # Переносим на GPU
            data_gpu = data.to(device, non_blocking=True)
            label_gpu = label.to(device, non_blocking=True)
            
            self.gpu_data.append(data_gpu)
            self.gpu_labels.append(label_gpu)
    
    def __len__(self):
        return len(self.gpu_data)
    
    def __getitem__(self, idx):
        return self.gpu_data[idx], self.gpu_labels[idx]
    
class GPUDataset(Dataset):
    def __init__(self, data_tensor, labels_tensor, labels_dict):
        self.gpu_data = data_tensor.to(device, non_blocking=True)
        self.gpu_labels = labels_tensor.to(device, non_blocking=True) 

        # множество тегов
        self.moodthemes = set()
        for tags in labels_dict.values():
            self.moodthemes.update(tags)

        # сортриуем и преобразуем теги в индексы
        self.moodthemes = sorted(list(self.moodthemes))
        self.tag_to_idx = {tag: idx for idx, tag in enumerate(self.moodthemes)}
        self.num_classes = len(self.moodthemes)

    def get_class_names(self):
        return self.moodthemes

    def __len__(self):
        return len(self.gpu_data)
    
    def __getitem__(self, idx):
        return self.gpu_data[idx], self.gpu_labels[idx]

def load_efficient(filename='../data/efficient_data.pth'):    
    data_dict = torch.load(filename)
    
    print(f"Данные загружены из {filename}")
    print(f"Данные: {data_dict['data'].shape}")
    print(f"Лейблы: {data_dict['labels'].shape}")
    
    if 'metadata' in data_dict:
        print(f"Классы: {data_dict['metadata']['num_classes']}")
    
    return data_dict['data'], data_dict['labels']

tags_dict = {}
# открываем подготовленный словрь
with open("../data/track_tags.pkl", 'rb') as file:
    tags_dict = pickle.load(file)

# для корректировки весов
pos_weight = []
with open("../data/pos_weight.pkl", "rb") as file:
    pos_weight = pickle.load(file).to(device)

data, labels = load_efficient('../data/0_efficient_data.pth')
dataset = GPUDataset(data, labels, tags_dict)

# разбиваем датасет на train и test
dataset_size = len(dataset)
indices = list(range(dataset_size))

train_idx, test_idx = train_test_split(
    indices, 
    test_size = 0.1,
    train_size = 0.5,       
    random_state = 42        # для воспроизводимости
)

train_dataset = Subset(dataset, train_idx)
test_dataset = Subset(dataset, test_idx)

train_loader = DataLoader(
    train_dataset,
    batch_size = 32,
    shuffle = True,
    num_workers = 0,
    pin_memory = False
)

test_loader = DataLoader(
    test_dataset,
    batch_size = 32,
    shuffle = False,
    num_workers = 0,
    pin_memory = False
)

total_vram_used = torch.cuda.memory_allocated('cuda') / 1024**3
print(f"Использовано VRAM: {total_vram_used:.2f} GB")

Данные загружены из ../data/0_efficient_data.pth
Данные: torch.Size([11091, 1, 128, 512])
Лейблы: torch.Size([11091, 59])
Классы: 59
Использовано VRAM: 2.71 GB


In [3]:
# тут будут классы моделей
from sklearn.metrics import hamming_loss

class AudioCNN(nn.Module):
    def __init__(self, num_classes):
        
        super(AudioCNN, self).__init__()
        #
        self.features = nn.Sequential(
            nn.Conv2d(1, 32, kernel_size=3, padding=1),
            nn.BatchNorm2d(32),
            nn.ReLU(),
            nn.MaxPool2d(2),
            
            nn.Conv2d(32, 64, kernel_size=3, padding=1),
            nn.BatchNorm2d(64),
            nn.ReLU(),
            nn.MaxPool2d(2),
            
            nn.Conv2d(64, 128, kernel_size=3, padding=1),
            nn.BatchNorm2d(128),
            nn.ReLU(),
            nn.MaxPool2d(2),

            nn.AdaptiveAvgPool2d((4,4))
        )

        #
        self.classifer = nn.Sequential(
            nn.Flatten(),
            nn.Linear(128 * 4 * 4, 512),
            nn.ReLU(),
            nn.Dropout(0.5),

            nn.Linear(512, 256),
            nn.ReLU(),
            nn.Dropout(0.3),

            nn.Linear(256, num_classes),
            nn.Sigmoid()
        )
    
    def forward(self, x):
        x = self.features(x)
        x = self.classifer(x)
        return x

class SimpleFCModel(nn.Module):
    def __init__(self, num_classes: int, input_height: int, input_width: int, hidden_size: int):
        super(SimpleFCModel, self).__init__()
        
        self.input_height = input_height
        self.input_width = input_width
        self.num_classes = num_classes
        
        # Вычисляем размер после вытягивания в вектор
        self.flatten_size = input_height * input_width
        
        self.layers = nn.Sequential(
            # Вытягиваем в плоский вектор
            nn.Flatten(),
            
            # Первый скрытый слой
            nn.Linear(self.flatten_size, hidden_size),
            nn.ReLU(),
            nn.Dropout(0.5),  # для регуляризации
            
            # Второй скрытый слой (можно добавить больше)
            nn.Linear(hidden_size, hidden_size // 2),
            nn.ReLU(), 
            nn.Dropout(0.4),
            
            # Выходной слой
            nn.Linear(hidden_size // 2, num_classes)
        )
    
    def forward(self, x):
        return self.layers(x)

def calculate_all_metrics(y_true, y_pred, loss=None, val_loss=None):
    
    metrics = {}
    
    # Loss
    metrics['loss'] = loss
    metrics['val_loss'] = val_loss

    # Exact Match метрика
    metrics['exact_match'] = (y_true == y_pred).all(axis=1).mean()
    metrics['hamming_loss'] = hamming_loss(y_true, y_pred)
    
    # F1 метрики
    metrics['f1_macro'] = f1_score(y_true, y_pred, average='macro', zero_division=0)
    metrics['f1_micro'] = f1_score(y_true, y_pred, average='micro', zero_division=0)
    metrics['f1_weighted'] = f1_score(y_true, y_pred, average='weighted', zero_division=0)
    
    # Статистика по тегам
    metrics['avg_predicted_tags'] = y_pred.sum(axis=1).mean()
    metrics['avg_true_tags'] = y_true.sum(axis=1).mean()
    metrics['samples_with_tags'] = (y_true.sum(axis=1) > 0).mean()
        
    return metrics

def train_epoch(model, loader, optimizer, criterion, treshold):
    model.train()
    total_loss = 0.0
    all_targets = []
    all_predictions = []
        
    for data, targets in loader:        
        
        optimizer.zero_grad()                           # Обнуляем градиенты
        outputs = model(data)                           # Прямой проход
        loss = criterion(outputs, targets)              # Вычисляем loss

        loss.backward()                                 # Обратный проход
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_norm=1.0)
        optimizer.step()                                 
        
        # Сохраняем предсказания и цели для метрик
        with torch.no_grad():                           
            predictions = (outputs > treshold).float()            
            all_targets.append(targets.cpu())           
            all_predictions.append(predictions.cpu())   

        total_loss += loss.item()

    all_targets = torch.cat(all_targets).numpy()
    all_predictions = torch.cat(all_predictions).numpy()
    
    total_loss /= len(loader)

    return calculate_all_metrics(all_targets, all_predictions, loss=total_loss)

def evaluate_epoch(model, loader, criterion, treshold):
    model.eval()
    total_loss = 0.0
    all_targets = []
    all_predictions = []
    
    with torch.no_grad():
        for data, targets in loader:            
            outputs = model(data)                       
            loss = criterion(outputs, targets)          
            predictions = (outputs > treshold).float()   

            all_targets.append(targets.cpu())          
            all_predictions.append(predictions.cpu())   
            
            total_loss += loss.item()                   # Обновляем статистику
    
    # Объединяем все батчи
    all_targets = torch.cat(all_targets).numpy()
    all_predictions = torch.cat(all_predictions).numpy()
    
    total_loss /= len(loader)
    
    return calculate_all_metrics(all_targets, all_predictions, val_loss=total_loss)

def train_model(model, train_loader, val_loader, optimizer, criterion, scheduler, 
                num_epochs=50, threshold=0.5, save_dir='../data/models'):

    os.makedirs(save_dir, exist_ok=True)
    
    history = {'train_loss': [], 'val_loss': [], 'train_f1_macro': [], 'val_f1_macro': [],
               'train_avg_predicted_tags':[], 'val_avg_predicted_tags':[],
                'train_avg_true_tags':[], 'val_avg_true_tags':[], 'learning_rate':[]}
    
    best_f1 = 0.0
    best_epoch = 0
    patience_counter = 0
    
    for epoch in range(1, num_epochs + 1):

        # Обучение и валидация
        train_metrics = train_epoch(model, train_loader, optimizer, criterion, threshold)
        val_metrics = evaluate_epoch(model, val_loader, criterion, threshold)
        
        # Сохраняем историю
        history['train_loss'].append(train_metrics['loss'])
        history['val_loss'].append(val_metrics['val_loss'])
        history['train_f1_macro'].append(train_metrics['f1_macro'])
        history['val_f1_macro'].append(val_metrics['f1_macro'])

        history['train_avg_predicted_tags'].append(train_metrics['avg_predicted_tags'])
        history['val_avg_predicted_tags'].append(val_metrics['avg_predicted_tags'])
        history['train_avg_true_tags'].append(train_metrics['avg_true_tags'])
        history['val_avg_true_tags'].append(val_metrics['avg_true_tags'])
        
        history['learning_rate'].append(optimizer.param_groups[0]['lr'])

        current_f1 = val_metrics['f1_macro']
        if scheduler is not None:
            old_lr = optimizer.param_groups[0]['lr']
            if isinstance(scheduler, torch.optim.lr_scheduler.ReduceLROnPlateau):
                scheduler.step(current_f1)
            else:
                scheduler.step()
        
        new_lr = optimizer.param_groups[0]['lr']
        if new_lr != old_lr:
            print(f"LR изменён на: {new_lr:.2e}")

        # Обновляем лучшую модель
        if current_f1 > best_f1:
            patience_counter = 0
            best_f1 = current_f1
            best_epoch = epoch
            torch.save({
                'epoch': epoch,
                'model_state_dict': model.state_dict(),
                'optimizer_state_dict': optimizer.state_dict(),
                'scheduler_state_dict': scheduler.state_dict() if scheduler else None,
                'val_f1_macro': best_f1,
                'threshold': threshold
            }, os.path.join(save_dir, 'FCmodel_best.pth'))
        else:
            patience_counter += 1

        if patience_counter >= scheduler.patience:
            print(f"Early stopping! Нет улучшений за {scheduler.patience} эпох")
            break
        
        clear_output(wait=True)
        
        print(f"Epoch: {epoch}/{num_epochs} | Best: {best_epoch} (F1: {best_f1:.4f}) | LR: {optimizer.param_groups[0]['lr']:.2e}")
        print("=" * 65)
        print(f"{'Metric':<15} | {'Train':<4} | {'Val':<4} ")
        print("-" * 65)
        
        metrics_data = [
            ('Loss', train_metrics['loss'], val_metrics['val_loss']),
            ('F1 Macro', train_metrics['f1_macro'], val_metrics['f1_macro']),
            ('F1 Micro', train_metrics['f1_micro'], val_metrics['f1_micro']),
            ('Exact Match', train_metrics['exact_match'], val_metrics['exact_match']),
            ('Avg Tags', train_metrics['avg_predicted_tags'], val_metrics['avg_predicted_tags']),
            ('True Tags', train_metrics['avg_true_tags'], val_metrics['avg_true_tags'])
        ]
        
        for name, train_val, val_val in metrics_data:            
            print(f"{name:<15} | {train_val:.4f} | {val_val:.4f} ")
        
        print("-" * 65)
        
        # Прогресс
        progress = 100*epoch/num_epochs
        bar_length = 20
        bar = '█' * int(progress/100*bar_length) + '░' * (bar_length - int(progress/100*bar_length))
        print(f"Progress: [{bar}] {progress:.1f}% | Patience: {patience_counter}/{scheduler.patience}")

    torch.save({
        'epoch': epoch,
        'model_state_dict': model.state_dict(),
        'optimizer_state_dict': optimizer.state_dict(),
        'scheduler_state_dict': scheduler.state_dict() if scheduler else None,
        'val_f1_macro': current_f1,
    }, os.path.join(save_dir, 'FCmodel_final.pth'))

    return history, best_f1

def load_model(model, checkpoint_path, optimizer=None, device='cuda', verbose=True):
    checkpoint = torch.load(checkpoint_path, map_location=device)
    
    # Загружаем веса модели
    model.load_state_dict(checkpoint['model_state_dict'])
    
    # Загружаем оптимизатор если нужно
    if optimizer is not None:
        optimizer.load_state_dict(checkpoint['optimizer_state_dict'])
        # Переносим состояние оптимизатора на правильное устройство
        for state in optimizer.state.values():
            for k, v in state.items():
                if isinstance(v, torch.Tensor):
                    state[k] = v.to(device)
    
    if verbose:
        print(f'Model loaded from {checkpoint_path}')
        print(f'Epoch: {checkpoint["epoch"]}')
        val_f1 = checkpoint.get('val_f1_macro', 'N/A')
        print(f'Val F1-macro: {val_f1:.4f}')
    
    return model

def plot_history(history, figsize=(15, 10)):
    epochs = range(1, len(history['train_loss']) + 1)
    
    # Создаем subplots
    fig, axes = plt.subplots(2, 2, figsize=figsize)
    fig.suptitle('Training History', fontsize=16, fontweight='bold')
    
    # 1. График Loss
    axes[0, 0].plot(epochs, history['train_loss'], 'b-', label='Train Loss', linewidth=2)
    axes[0, 0].plot(epochs, history['val_loss'], 'r-', label='Val Loss', linewidth=2)
    axes[0, 0].set_title('Loss')
    axes[0, 0].set_xlabel('Epoch')
    axes[0, 0].set_ylabel('Loss')
    axes[0, 0].legend()
    axes[0, 0].grid(True, alpha=0.3)
    
    # 2. График Accuracy
    axes[0, 1].plot(epochs, history['train_accuracy'], 'b-', label='Train Accuracy', linewidth=2)
    axes[0, 1].plot(epochs, history['val_accuracy'], 'r-', label='Val Accuracy', linewidth=2)
    axes[0, 1].set_title('Accuracy')
    axes[0, 1].set_xlabel('Epoch')
    axes[0, 1].set_ylabel('Accuracy')
    axes[0, 1].legend()
    axes[0, 1].grid(True, alpha=0.3)
    axes[0, 1].set_ylim(0, 1)
    
    # 3. График F1-score
    axes[1, 0].plot(epochs, history['train_f1'], 'b-', label='Train F1', linewidth=2)
    axes[1, 0].plot(epochs, history['val_f1'], 'r-', label='Val F1', linewidth=2)
    axes[1, 0].set_title('F1-Score (Macro)')
    axes[1, 0].set_xlabel('Epoch')
    axes[1, 0].set_ylabel('F1-Score')
    axes[1, 0].legend()
    axes[1, 0].grid(True, alpha=0.3)
    axes[1, 0].set_ylim(0, 1)
    
    # 4. Сводный график всех метрик (валидация) - ИСПРАВЛЕННАЯ ЧАСТЬ
    axes[1, 1].plot(epochs, history['val_accuracy'], 'g-', label='Val Accuracy', linewidth=2)
    axes[1, 1].plot(epochs, history['val_f1'], 'orange', label='Val F1', linewidth=2)
    
    # ИСПРАВЛЕНИЕ: преобразуем в numpy array перед делением
    val_loss = np.array(history['val_loss'])
    if max(val_loss) > 0:  # Проверяем чтобы не делить на 0
        val_loss_norm = val_loss / max(val_loss)
    else:
        val_loss_norm = val_loss
    
    axes[1, 1].plot(epochs, val_loss_norm, 'r-', label='Val Loss (norm)', linewidth=2)
    axes[1, 1].set_title('Validation Metrics Summary')
    axes[1, 1].set_xlabel('Epoch')
    axes[1, 1].set_ylabel('Value')
    axes[1, 1].legend()
    axes[1, 1].grid(True, alpha=0.3)
    
    plt.tight_layout()
    plt.show()
    
    # Выводим лучшие значения
    best_val_acc = max(history['val_accuracy'])
    best_val_f1 = max(history['val_f1'])
    best_epoch_acc = history['val_accuracy'].index(best_val_acc) + 1
    best_epoch_f1 = history['val_f1'].index(best_val_f1) + 1
    
    print("Training Results Summary:")
    print(f"Best Validation Accuracy: {best_val_acc:.4f} (epoch {best_epoch_acc})")
    print(f"Best Validation F1-Score: {best_val_f1:.4f} (epoch {best_epoch_f1})")
    print(f"Final Validation Loss: {history['val_loss'][-1]:.4f}")
    print(f"Final Train Accuracy: {history['train_accuracy'][-1]:.4f}")
    print(f"Final Train F1: {history['train_f1'][-1]:.4f}")

def plot_quick_history(history, figsize=(12, 8)):
    fig, (ax1, ax2, ax3) = plt.subplots(1, 3, figsize=figsize)
    fig.suptitle('Ключевые метрики обучения', fontsize=14, fontweight='bold')
    
    epochs = range(1, len(history['train_loss']) + 1)
    
    # Loss
    ax1.plot(epochs, history['train_loss'], 'b-', label='Train', linewidth=2)
    if 'val_loss' in history:
        ax1.plot(epochs, history['val_loss'], 'r-', label='Val', linewidth=2)
    ax1.set_title('Loss')
    ax1.set_xlabel('Эпоха')
    ax1.legend()
    ax1.grid(True, alpha=0.3)
    
    # F1 Macro
    if 'train_f1_macro' in history:
        ax2.plot(epochs, history['train_f1_macro'], 'b-', label='Train', linewidth=2)
    if 'val_f1_macro' in history:
        ax2.plot(epochs, history['val_f1_macro'], 'r-', label='Val', linewidth=2)
    ax2.set_title('F1 Macro')
    ax2.set_xlabel('Эпоха')
    ax2.set_ylim(0, 1)
    ax2.legend()
    ax2.grid(True, alpha=0.3)
    
    # Avg Tags
    if 'train_avg_predicted_tags' in history:
        ax3.plot(epochs, history['train_avg_predicted_tags'], 'b-', label='Train', linewidth=2)
    if 'val_avg_predicted_tags' in history:
        ax3.plot(epochs, history['val_avg_predicted_tags'], 'r-', label='Val', linewidth=2)
        ax3.set_title('Avg Tags per Sample')
        ax3.set_xlabel('Эпоха')
        ax3.set_ylabel('Количество тегов')
        ax3.grid(True, alpha=0.3)
        ax3.legend()
    
    # plt.tight_layout()
    plt.show()

def calculate_pos_weight(dataset, device):
    all_targets = []
    for i in range(len(dataset)):
        _, targets = dataset[i]
        all_targets.append(targets)

    all_targets = torch.stack(all_targets)

    # Вычисляем веса: negative_count / positive_count
    positive_counts = all_targets.sum(dim=0)
    negative_counts = len(dataset) - positive_counts

    # Избегаем деления на 0
    pos_weight = negative_counts / (positive_counts + 1e-6)

    print("Рассчитанные pos_weight:")
    for i, (weight, pos_count) in enumerate(zip(pos_weight, positive_counts)):
        if pos_count > 0:
            print(f"   Класс {i}: вес {weight:.2f}, позитивных: {pos_count.item()}")

    return pos_weight.to(device) 


In [4]:
num_epochs = 100            # количество эпох для обучения
threshold = 0.75             # для предсказаний
patience = 100               # остановка обучения после N эпох без улучшений

# Инициализация модели
model = AudioCNN(dataset.num_classes).to(device)

criterion = nn.BCEWithLogitsLoss(pos_weight=pos_weight) #pos_weight=pos_weight
optimizer = torch.optim.Adam(model.parameters(), lr=1e-4, weight_decay=1e-4)
scheduler = torch.optim.lr_scheduler.ReduceLROnPlateau(
    optimizer,
    mode='max',
    patience=patience,
    factor=0.5
)

print(f"Используется устройство: {device}")

print(f"Количество параметров модели: {sum(p.numel() for p in model.parameters())}")

# Загрузка модели
model = load_model(
    model=model,
    checkpoint_path="../data/models/FCmodel_best.pth",
    optimizer=optimizer
)

# Запуск обучения
history, best_f1 = train_model(
    model=model,
    train_loader=train_loader,
    val_loader=test_loader,
    optimizer=optimizer,
    criterion=criterion,
    scheduler=scheduler,
    num_epochs=num_epochs,
    threshold = threshold,
    save_dir='../data/models'
)

# вывод графиков
plot_quick_history(history)

Используется устройство: cuda
Количество параметров модели: 1288699
Model loaded from ../data/models/FCmodel_best.pth
Epoch: 72
Val F1-macro: 0.1535


KeyboardInterrupt: 

In [ ]:
# def quick_predict(model, audio_path, preprocess_function, class_names, device='cuda', treshold = 0.5):
#     # Убедимся, что модель на правильном устройстве
#     model.to(device)
#     model.eval()
    
#     try:
#         # Препроцессинг
#         mel_spec = preprocess_function(audio_path)
        
#         # Добавляем batch dimension и перемещаем на устройство
#         if len(mel_spec.shape) == 3:  # [channels, height, width]
#             input_tensor = mel_spec.unsqueeze(0)  # [1, channels, height, width]
#         else:
#             input_tensor = mel_spec.unsqueeze(0).unsqueeze(0)  # [1, 1, height, width]
        
#         input_tensor = input_tensor.to(device)
        
#         # Предсказание
#         with torch.no_grad():
#             outputs = model(input_tensor)
#             probs = torch.sigmoid(outputs).cpu().numpy()[0]
        
#         # Результаты
#         print(f"\n Prediction for: {os.path.basename(audio_path)}")
        
#         active_tags = []
#         for i, (class_name, prob) in enumerate(zip(class_names, probs)):
#             if prob > treshold:
#                 print(f"  -- {class_name}: {prob:.3f}")
#                 active_tags.append(class_name)
        
#         if not active_tags:
#             print(f" No tags predicted above 0.5 threshold")
            
#         return probs, active_tags
        
#     except Exception as e:
#         print(f"Error during prediction: {e}")
#         return None, None

# best_model = AudioCNN(num_classes=dataset.num_classes)

# load_model(best_model, '../data/models/FCmodel_best.pth')
# best_model.to(device)
# best_model.eval()


# test_audio_path = "../data/train/" + "00/7400.mp3"

# quick_predict(
#     model=best_model,
#     audio_path=test_audio_path,
#     preprocess_function=preprocess_audio,
#     class_names=dataset.get_class_names(),
#     device=device,
#     treshold = 0.6
# )

In [5]:
import random
import glob
from IPython.display import Audio, display

def random_audio_predictor(model, preprocess_function, class_names, folder_path='../data/train/', device='cuda', threshold=0.5):
    """
    Случайный выбор аудио файла с автовоспроизведением и предсказанием тегов
    """
    
    print("🎲 СЛУЧАЙНЫЙ АУДИО АНАЛИЗ")
    print("=" * 50)
    
    # Находим все аудио файлы в папке
    audio_extensions = ['*.wav', '*.mp3', '*.flac', '*.m4a', '*.ogg']
    audio_files = []
    
    for ext in audio_extensions:
        # Ищем файлы в основной папке и подпапках
        audio_files.extend(glob.glob(os.path.join(folder_path, '**', ext), recursive=True))
        audio_files.extend(glob.glob(os.path.join(folder_path, ext)))
    
    if not audio_files:
        print(f"❌ В папке {folder_path} не найдено аудио файлов!")
        return None
    
    print(f"📁 Папка: {folder_path}")
    print(f"📊 Найдено файлов: {len(audio_files)}")
    print(f"🎚️  Порог: {threshold}")
    
    # Выбираем случайный файл
    selected_file = random.choice(audio_files)
    filename = os.path.basename(selected_file)
    file_path = os.path.dirname(selected_file)
    
    print(f"\n🎯 Выбран файл: {filename}")
    print(f"📂 Путь: {file_path}")
    print("─" * 50)
    
    try:
        # Автовоспроизведение аудио
        print("🔊 Автовоспроизведение...")
        display(Audio(selected_file, autoplay=True))
        
        # Предсказание тегов
        print("\n🤖 Анализ тегов...")
        probs, active_tags = quick_predict(
            model=model,
            audio_path=selected_file,
            preprocess_function=preprocess_function,
            class_names=class_names,
            device=device,
            threshold=threshold
        )
        
        if probs is not None:
            # Выводим результаты
            print(f"\n🏷️  ПРЕДСКАЗАННЫЕ ТЕГИ:")
            print("─" * 30)
            
            if active_tags:
                print(f"✅ Найдено тегов: {len(active_tags)}")
                print("\n📋 Список тегов:")
                for tag in active_tags:
                    prob = probs[class_names.index(tag)]
                    print(f"   • {tag}: {prob:.3f}")
            else:
                print("❌ Нет тегов выше порога")
            
            # Топ-10 всех предсказаний
            top_indices = np.argsort(probs)[::-1][:10]
            print(f"\n🔝 Топ-10 всех предсказаний:")
            for i, idx in enumerate(top_indices, 1):
                prob = probs[idx]
                tag = class_names[idx]
                marker = "✅" if prob > threshold else "  "
                print(f"   {i:2d}. {marker} {tag:<25} {prob:.3f}")
            
            # Статистика
            print(f"\n📊 СТАТИСТИКА:")
            print(f"   Всего возможных тегов: {len(class_names)}")
            print(f"   Активных тегов: {len(active_tags)}")
            print(f"   Максимальная вероятность: {max(probs):.3f}")
            print(f"   Средняя вероятность: {np.mean(probs):.3f}")
            
            return {
                'file': selected_file,
                'filename': filename,
                'probs': probs,
                'active_tags': active_tags,
                'threshold': threshold
            }
        else:
            print("❌ Ошибка при предсказании тегов")
            return None
            
    except Exception as e:
        print(f"❌ Ошибка: {e}")
        return None

def quick_predict(model, audio_path, preprocess_function, class_names, device='cuda', threshold=0.5):
    """
    Функция предсказания тегов для аудио файла
    """
    model.to(device)
    model.eval()
    
    try:
        # Препроцессинг
        mel_spec = preprocess_function(audio_path)
        
        # Добавляем batch dimension и перемещаем на устройство
        if len(mel_spec.shape) == 3:  # [channels, height, width]
            input_tensor = mel_spec.unsqueeze(0)  # [1, channels, height, width]
        else:
            input_tensor = mel_spec.unsqueeze(0).unsqueeze(0)  # [1, 1, height, width]
        
        input_tensor = input_tensor.to(device)
        
        # Предсказание
        with torch.no_grad():
            outputs = model(input_tensor)
            probs = torch.sigmoid(outputs).cpu().numpy()[0]
        
        # Собираем активные теги
        active_tags = []
        for i, (class_name, prob) in enumerate(zip(class_names, probs)):
            if prob > threshold:
                active_tags.append(class_name)
        
        return probs, active_tags
        
    except Exception as e:
        print(f"❌ Ошибка во время предсказания: {e}")
        return None, None

best_model = AudioCNN(num_classes=dataset.num_classes)
load_model(best_model, '../data/models/FCmodel_best.pth')
best_model.to(device)
best_model.eval()

# Простой вызов - один случайный файл
random_audio_predictor(
    model=best_model,
    preprocess_function=preprocess_audio,
    class_names=dataset.get_class_names(),
    folder_path='/home/egr/Музыка',  # Ваша папка с аудио
    device=device,
    threshold=0.7  # Можно настроить порог
)


Model loaded from ../data/models/FCmodel_best.pth
Epoch: 72
Val F1-macro: 0.1535
🎲 СЛУЧАЙНЫЙ АУДИО АНАЛИЗ
📁 Папка: /home/egr/Музыка
📊 Найдено файлов: 2
🎚️  Порог: 0.7

🎯 Выбран файл: MAISONdes-Bake-no-Kawa-_GNOSIA-Opening_-ft.-Kobo-Kanaeru_-Kasane-Teto_-Giga_-TeddyLoid.mp3
📂 Путь: /home/egr/Музыка
──────────────────────────────────────────────────
🔊 Автовоспроизведение...



🤖 Анализ тегов...

🏷️  ПРЕДСКАЗАННЫЕ ТЕГИ:
──────────────────────────────
✅ Найдено тегов: 3

📋 Список тегов:
   • energetic: 0.730
   • heavy: 0.719
   • powerful: 0.725

🔝 Топ-10 всех предсказаний:
    1. ✅ energetic                 0.730
    2. ✅ powerful                  0.725
    3. ✅ heavy                     0.719
    4.    sport                     0.663
    5.    upbeat                    0.658
    6.    game                      0.621
    7.    fast                      0.618
    8.    ambiental                 0.567
    9.    dark                      0.564
   10.    melodic                   0.547

📊 СТАТИСТИКА:
   Всего возможных тегов: 59
   Активных тегов: 3
   Максимальная вероятность: 0.730
   Средняя вероятность: 0.525


{'file': '/home/egr/Музыка/MAISONdes-Bake-no-Kawa-_GNOSIA-Opening_-ft.-Kobo-Kanaeru_-Kasane-Teto_-Giga_-TeddyLoid.mp3',
 'filename': 'MAISONdes-Bake-no-Kawa-_GNOSIA-Opening_-ft.-Kobo-Kanaeru_-Kasane-Teto_-Giga_-TeddyLoid.mp3',
 'probs': array([0.5001439 , 0.5000321 , 0.5001899 , 0.56698036, 0.5000049 ,
        0.50000024, 0.50000024, 0.5000149 , 0.5000807 , 0.50000936,
        0.5000389 , 0.50012076, 0.5637165 , 0.5002791 , 0.50002146,
        0.5       , 0.5000001 , 0.50017035, 0.5004566 , 0.7298348 ,
        0.5000829 , 0.6182666 , 0.50014085, 0.51802   , 0.5151234 ,
        0.62101424, 0.50032574, 0.5027331 , 0.7194376 , 0.5001205 ,
        0.50000006, 0.501174  , 0.5000018 , 0.50109035, 0.50000274,
        0.5000007 , 0.5000339 , 0.54693806, 0.50000644, 0.5000001 ,
        0.5       , 0.51059544, 0.5000142 , 0.72532004, 0.5       ,
        0.50000024, 0.50000006, 0.50000733, 0.51269156, 0.5       ,
        0.5       , 0.500102  , 0.5007584 , 0.6630006 , 0.5015649 ,
        0.500001